## 13번 모델
- ray 
- fillna
- baseline prohet 
    - changepoint_prior_scale = 0.05 -> T + SS 에서만 0.01
    - seasonality_prior_scale = 10 디폴트
- results- ray 

---
pH에선 로스 증가
COD 에서도 로스 감소

---
## 파라미터 설명 참조 
https://velog.io/@choijhyeok/Prophet-1-parameter-%EC%95%8C%EC%95%84%EB%B3%B4%EA%B8%B0

In [6]:
import ray

In [7]:
# 라이브러리 임포트
import os
import time
import json
import datetime
import numpy as np
import pandas as pd
from fbprophet import Prophet
import pickle
import copy
import time
from functools import *
from tqdm.auto import tqdm

In [8]:
%%time
''' 베이스라인 코드에서 json으로 DF만듬. 이미 만들어진 데이터를 로드 '''
submit = json.load(open('./data/sample_submission/sample_submission.json', 'r', encoding='utf8')) 
df_dic = pickle.load(open('./mydata/df_dic.plk','rb')) # 모든 측정 지점의 피쳐 값들 
plc_lst = pickle.load(open('./mydata/plc_lst.plk','rb')) # 측정 지점 리스트
fct_lst = ['pH', 'COD', 'SS', 'N', 'P', 'T'] # 피쳐 리스트

CPU times: user 782 ms, sys: 96.1 ms, total: 878 ms
Wall time: 879 ms


---
## 데이터 전처리 

In [4]:
%%time
''' fillna : 단순 missing value 채움'''
for plc in plc_lst:
    df = df_dic[plc]
    df = df.fillna(method='ffill')
    df = df.fillna(method='bfill')    
    df_dic[plc] = df.dropna()
    
    if df_dic[plc].isna().any().any():
        print(plc)

CPU times: user 2.23 s, sys: 8.04 ms, total: 2.23 s
Wall time: 2.24 s


---
## 모델 훈련

In [9]:
''' Prophet 예측을 위한 dataframe 포맷 제작 '''
future = pd.DataFrame([str(x)[:10] for x in list(pd.date_range(start='2018-02-01', end='2019-12-31', inclusive="both"))], columns=['ds'])
future['y'] = np.nan
#future

In [10]:
@ray.remote
def pred_all_columns_chunk(plc_lst_partial,df_dic,fct_lst):
    res_list = []
    for i in plc_lst_partial:
        plc_df= df_dic[i]
        for j in fct_lst: # 피쳐 리스트
            fct_df = plc_df[['ds', j]]   # 날짜 - 피쳐1 조합임.
            fct_df = fct_df.rename(columns={j:'y'}) # 피쳐1을 y로 바꾼다.
            
            if j in ['SS,'' T']:
                model = Prophet(
                    changepoint_prior_scale = 0.01,)
            else:
                 model = Prophet()
                    
            model.fit(fct_df)
            forecast = model.predict(future)
            forecast['ds'] = forecast['ds'].apply(lambda x : str(x).split(' ')[0].split('-')[0]+str(x).split(' ')[0].split('-')[1]+str(x).split(' ')[0].split('-')[2])
            forecast = forecast[['ds', 'yhat']]

            #for index, k in enumerate(list(forecast['ds'])):
            #    submit[i][forecast.loc[index, 'ds']][j] = np.float(forecast[forecast['ds']==k]['yhat'])

            res_list.append( (i,j,forecast) )
    return res_list

In [11]:
fct_lst_ray = ray.put(fct_lst)
df_dic_ray = ray.put(df_dic)

In [12]:
''' plc_lst 를 나눠서 병렬처리 '''
plc_splited = [list(x) for x in  list(np.array_split(plc_lst, 48 ))] # 48코어

In [13]:
''' 주의 : 백그라운드에서 돌아가므로, 
cpu 로드율을 보고, 로드율이 100% 가까이 올라갔다가, 
아이들링 수치로 떨어졌을때 작업이 끝난거임. 
그전에는 다음 코드를 실행하지 말것. '''
task_list = [ pred_all_columns_chunk.remote(x,df_dic_ray,fct_lst_ray) for x in plc_splited ]

(pred_all_columns_chunk pid=39215) INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
(pred_all_columns_chunk pid=39215) /ssd/jaewoo/anaconda3/envs/ts/lib/python3.9/site-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
(pred_all_columns_chunk pid=39215)   components = components.append(new_comp)
(pred_all_columns_chunk pid=39206) INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
(pred_all_columns_chunk pid=39206) /ssd/jaewoo/anaconda3/envs/ts/lib/python3.9/site-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
(pred_all_columns_chunk pid=39206)   components = components.append(new_comp)
(pred_all_columns_chunk pid=39221) INFO:fbprophet:Disabling 

(pred_all_columns_chunk pid=39215) Initial log joint probability = -84.0903
(pred_all_columns_chunk pid=39215)     Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
(pred_all_columns_chunk pid=39206) Initial log joint probability = -38.3705
(pred_all_columns_chunk pid=39206)     Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 


(pred_all_columns_chunk pid=39211) INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
(pred_all_columns_chunk pid=39211) /ssd/jaewoo/anaconda3/envs/ts/lib/python3.9/site-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
(pred_all_columns_chunk pid=39211)   components = components.append(new_comp)
(pred_all_columns_chunk pid=39206) /ssd/jaewoo/anaconda3/envs/ts/lib/python3.9/site-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
(pred_all_columns_chunk pid=39206)   components = components.append(new_comp)
(pred_all_columns_chunk pid=39213) INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
(pred_all_columns_chunk pid=39213) /ssd/jaewoo/anaconda3/env

(pred_all_columns_chunk pid=39211) Initial log joint probability = -30.0277
(pred_all_columns_chunk pid=39211)     Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
(pred_all_columns_chunk pid=39206)       76       1576.03   1.59205e-05       62.1784   4.056e-07       0.001      138  LS failed, Hessian reset 
(pred_all_columns_chunk pid=39206)       99       1576.03   6.40052e-06       47.9393      0.1974      0.1974      171   
(pred_all_columns_chunk pid=39206)     Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
(pred_all_columns_chunk pid=39206)      105       1576.03   3.69943e-06       66.1348   5.853e-08       0.001      217  LS failed, Hessian reset 
(pred_all_columns_chunk pid=39206)      117       1576.03   1.07696e-08       43.3679    0.002118      0.4759      238   
(pred_all_columns_chunk pid=39206) Optimization terminated normally: 
(pred_all_columns_chunk pid=39206)   Convergence detected: relat

(pred_all_columns_chunk pid=39222) INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
(pred_all_columns_chunk pid=39237) INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
(pred_all_columns_chunk pid=39237) /ssd/jaewoo/anaconda3/envs/ts/lib/python3.9/site-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
(pred_all_columns_chunk pid=39237)   components = components.append(new_comp)
(pred_all_columns_chunk pid=39216) INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
(pred_all_columns_chunk pid=39216) /ssd/jaewoo/anaconda3/envs/ts/lib/python3.9/site-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
(

...

(pred_all_columns_chunk pid=39216)      399       2732.38    0.00129977       106.694      0.2854      0.7721      553   
(pred_all_columns_chunk pid=39216)     Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
(pred_all_columns_chunk pid=39222)      522       3339.27    0.00021076       155.375   2.569e-06       0.001      726  LS failed, Hessian reset 
(pred_all_columns_chunk pid=39222)      560       3339.38   0.000116933       105.365   1.314e-06       0.001      810  LS failed, Hessian reset 
(pred_all_columns_chunk pid=39222)      599       3339.44    0.00166618       72.1061           1           1      855   
(pred_all_columns_chunk pid=39222)     Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
(pred_all_columns_chunk pid=39224)      199       2726.02    0.00135445       72.2543      0.9836      0.9836      255   
(pred_all_columns_chunk pid=39224)     Iter      log prob        ||dx||      ||grad||   

(pred_all_columns_chunk pid=39237) INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
(pred_all_columns_chunk pid=39237) /ssd/jaewoo/anaconda3/envs/ts/lib/python3.9/site-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
(pred_all_columns_chunk pid=39237)   components = components.append(new_comp)
(pred_all_columns_chunk pid=39251) INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
(pred_all_columns_chunk pid=39212) /ssd/jaewoo/anaconda3/envs/ts/lib/python3.9/site-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
(pred_all_columns_chunk pid=39212)   components = components.append(new_comp)
(pred_all_columns_chunk pid=39212) /ssd/jaewoo/anaconda3/env

(pred_all_columns_chunk pid=39232)     1111       5061.52   0.000187065       89.9878   2.687e-06       0.001     1827  LS failed, Hessian reset 
(pred_all_columns_chunk pid=39237)       99        5954.2     0.0050972       519.508           1           1      116   
(pred_all_columns_chunk pid=39237)     Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
(pred_all_columns_chunk pid=39246)      257       5786.18   8.46898e-05       61.4073   6.711e-07       0.001      335  LS failed, Hessian reset 
(pred_all_columns_chunk pid=39251)       99       3461.09     0.0150641       216.116           1           1      126   
(pred_all_columns_chunk pid=39251)     Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
(pred_all_columns_chunk pid=39216)      626       2743.01   0.000383572       81.1233   1.763e-06       0.001      906  LS failed, Hessian reset 
(pred_all_columns_chunk pid=39217)      139       1600.27    0.0

(pred_all_columns_chunk pid=39218) /ssd/jaewoo/anaconda3/envs/ts/lib/python3.9/site-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
(pred_all_columns_chunk pid=39218)   components = components.append(new_comp)
(pred_all_columns_chunk pid=39214) INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
(pred_all_columns_chunk pid=39214) /ssd/jaewoo/anaconda3/envs/ts/lib/python3.9/site-packages/fbprophet/forecaster.py:891: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
(pred_all_columns_chunk pid=39214)   components = components.append(new_comp)
(pred_all_columns_chunk pid=39255) INFO:fbprophet:Disabling daily seasonality. Run prophet with daily_seasonality=True to override this.
(pred_all_columns_chunk pid=39255) /ssd/jaewoo/anaconda3/env

(pred_all_columns_chunk pid=39216)      763       2744.49   2.10443e-05       60.4307   3.567e-07       0.001     1178  LS failed, Hessian reset 
(pred_all_columns_chunk pid=39216)      799        2744.5   0.000283945       57.6428           1           1     1229   
(pred_all_columns_chunk pid=39216)     Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
(pred_all_columns_chunk pid=39214)       78       2012.71   0.000777167       81.3614    9.53e-06       0.001      135  LS failed, Hessian reset 
(pred_all_columns_chunk pid=39214)       99       2012.79   3.30436e-05       67.3374      0.9325      0.9325      161   
(pred_all_columns_chunk pid=39214)     Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
(pred_all_columns_chunk pid=39214)      106       2012.82   0.000371286       65.9715   4.491e-06       0.001      207  LS failed, Hessian reset 
(pred_all_columns_chunk pid=39210)      459       2033.84   3.29

In [10]:
''' 결과 합치기 '''
results = ray.get(task_list)
results_combined = list(reduce(lambda f ,s : f +s ,results))

---
## TEST 데이터 포멧으로 바꾸기

In [11]:
%%time
''' 결과정리.'''
res_splited = [list(x) for x in  list(np.array_split(results_combined, 545 ))] # 48코어

for items in res_splited:
    df_lst = []
    for pred_info in items:
        comname = pred_info[0]
        col_name = pred_info[1]
        
        df_pred = pred_info[2]
        df_pred.columns = ['ds',col_name]
        df_lst.append(df_pred)
    df_combined = pd.concat(df_lst,axis = 1)
    df_sample = df_combined.loc[:, ~df_combined.columns.duplicated()]
    df_sample.index = df_sample.ds
    df_sample = df_sample.drop(['ds'],axis = 1)
    
    submit[comname] = df_sample.to_dict('index')

/ssd/jaewoo/anaconda3/envs/ts/lib/python3.9/site-packages/numpy/core/_asarray.py:102: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return array(a, dtype, copy=False, order=order)


CPU times: user 1.78 s, sys: 0 ns, total: 1.78 s
Wall time: 1.78 s


In [12]:
# 추론 파일 저장
with open('./sub/15_bs_fillna_cp0_01onlySS_T.json', 'w', encoding='utf8') as f:
    json.dump(submit, f, ensure_ascii=False)